In [ ]:
!nvidia-smi -L

Mount Google Drive to save sample levels as they are generated.

In [1]:
from google.colab import drive
drive.mount('/content/gdrive')

Go to this URL in a browser: https://accounts.google.com/o/oauth2/auth?client_id=947318989803-6bn6qk8qdgf4n4g3pfee6491hc0brc4i.apps.googleusercontent.com&redirect_uri=urn%3aietf%3awg%3aoauth%3a2.0%3aoob&response_type=code&scope=email%20https%3a%2f%2fwww.googleapis.com%2fauth%2fdocs.test%20https%3a%2f%2fwww.googleapis.com%2fauth%2fdrive%20https%3a%2f%2fwww.googleapis.com%2fauth%2fdrive.photos.readonly%20https%3a%2f%2fwww.googleapis.com%2fauth%2fpeopleapi.readonly

Enter your authorization code:
··········
Mounted at /content/gdrive


Prepare the environment.

In [2]:
!pip install git+https://github.com/robinsloan/jukebox.git

  Cloning https://github.com/robinsloan/jukebox.git to /tmp/pip-req-build-d7t7wips
  Running command git clone -q https://github.com/robinsloan/jukebox.git /tmp/pip-req-build-d7t7wips
     |████████████████████████████████| 61kB 3.3MB/s 
     |████████████████████████████████| 245kB 8.8MB/s 
     |████████████████████████████████| 1.6MB 10.3MB/s 
     |████████████████████████████████| 1.4MB 19.8MB/s 
  Created wheel for jukebox: filename=jukebox-1.0-cp36-none-any.whl size=198132 sha256=4e96cd3464a143e0949f83a6e6c1b6b7c74e92b57a92ff890367d524a7e37507
  Stored in directory: /tmp/pip-ephem-wheel-cache-ii7vc3v3/wheels/8c/12/fd/8d4c316f741ab49ebf38b3845548a1bdcb580e32e58ddf2bb5
  Created wheel for fire: filename=fire-0.1.3-py2.py3-none-any.whl size=49704 sha256=2452bd892173e6dc3e1c976c54df20dc759c133db61a0498426aca6f2a5574df
  Stored in directory: /root/.cache/pip/wheels/2a/1a/4d/6b30377c3051e76559d1185c1dbbfff15aed31f87acdd14c22
  Created wheel for librosa: filename=librosa-0.7.2-cp36-non

In [15]:
import jukebox
import torch as t
import librosa
import os
import pickle

from IPython.display import Audio
from jukebox.make_models import make_vqvae, make_prior, MODELS, make_model
from jukebox.hparams import Hyperparams, setup_hparams
from jukebox.sample import sample_single_window, _sample, \
                           sample_partial_window, upsample, \
                           load_prompts
from jukebox.utils.dist_utils import setup_dist_from_mpi
from jukebox.utils.torch_utils import empty_cache
rank, local_rank, device = setup_dist_from_mpi()

Caught error during NCCL init (attempt 0 of 5): trying to initialize the default process group twice!
Caught error during NCCL init (attempt 1 of 5): trying to initialize the default process group twice!
Caught error during NCCL init (attempt 2 of 5): trying to initialize the default process group twice!
Caught error during NCCL init (attempt 3 of 5): trying to initialize the default process group twice!
Caught error during NCCL init (attempt 4 of 5): trying to initialize the default process group twice!


RuntimeError: ignored

# Co-Composing with the 5B or 1B Lyrics Model

In [4]:
this_run_slug = "jul23_1"

model = "5b_lyrics" # or "1b_lyrics"
hps = Hyperparams()
hps.sr = 44100
hps.n_samples = 3 if model=='5b_lyrics' else 16
# Specifies the directory to save the sample in.
# We set this to the Google Drive mount point.

hps.name = '/content/gdrive/My Drive/samples/' + this_run_slug + '/'

if not os.path.exists(hps.name):
  os.makedirs(hps.name)

hps.sample_length = 1048576 if model=="5b_lyrics" else 786432 
chunk_size = 16 if model=="5b_lyrics" else 32
max_batch_size = 3 if model=="5b_lyrics" else 16
hps.hop_fraction = [.5, .5, .125] 
hps.levels = 3

In [5]:
vqvae, *priors = MODELS[model]
vqvae = make_vqvae(setup_hparams(vqvae, dict(sample_length = hps.sample_length)), device)
top_prior = make_prior(setup_hparams(priors[-1], dict()), vqvae, device)

Restored from /root/.cache/jukebox-assets/models/5b/vqvae.pth.tar
0: Loading vqvae in eval mode
Loading artist IDs from /usr/local/lib/python3.6/dist-packages/jukebox/data/ids/v2_artist_ids.txt
Loading artist IDs from /usr/local/lib/python3.6/dist-packages/jukebox/data/ids/v2_genre_ids.txt
Level:2, Cond downsample:None, Raw to tokens:128, Sample length:1048576
0: Converting to fp16 params
Restored from /root/.cache/jukebox-assets/models/5b_lyrics/prior_level_2.pth.tar
0: Loading prior in eval mode


Choose your artist, genre, and lyrics here!

In [53]:
total_sample_length_in_seconds = 120

metas_1 = [dict(artist = "Depeche Mode",
            genre = "Synthpop",
            total_length = total_sample_length_in_seconds * hps.sr,
            offset = 0,
            lyrics = """Love songs aren't about love, they're about love songs.
            Oh, love songs aren't about love, they're about love songs.

            No, love songs were never about love, never ever ever about love
            Just about all those other love songs

            Love songs aren't about love, they're about love songs.
            So, love songs aren't about love, they're about love songs.

            Baby, this song isn't about you, it's about a love song.
            A love song I heard long ago... now I'm singing mine, too.
            """,),
          ] * hps.n_samples

metas_2 = [dict(artist = "Frank Sinatra",
  genre = "Synthpop",
  total_length = total_sample_length_in_seconds * hps.sr,
  offset = 0,
  lyrics = "",),
] * hps.n_samples

pickle.dump( [metas_1, metas_2], open( f'{hps.name}meta.p', "wb" ) )

labels_1 = [None, None, top_prior.labeller.get_batch_labels(metas_1, 'cuda')]
labels_2 = [None, None, top_prior.labeller.get_batch_labels(metas_2, 'cuda')]

## Generate 3 options for the start of the song

Initial generation is set to be 4 seconds long, but feel free to change this

In [7]:
def seconds_to_tokens(sec, sr, prior, chunk_size):
  tokens = sec * hps.sr // prior.raw_to_tokens
  tokens = ((tokens // chunk_size) + 1) * chunk_size
  assert tokens <= prior.n_ctx, 'Choose a shorter generation length to stay within the top prior context'
  return tokens

In [8]:
initial_generation_in_seconds = 4
tokens_to_sample = seconds_to_tokens(initial_generation_in_seconds, hps.sr, top_prior, chunk_size)

Change the sampling temperature if you like (higher is more random).  Our favorite is in the range .98 to .995

In [9]:
sampling_temperature = 0.98
sampling_kwargs = dict(temp=sampling_temperature, fp16=True,
                       max_batch_size=max_batch_size, chunk_size=chunk_size)

In [10]:
# trying to work the priming in here...

audio_file = '/content/gdrive/My Drive/samples/best_one_yet_aud.wav'
audio_files = audio_file.split(',')
prompt_length_in_seconds = 7.0
duration = (int(prompt_length_in_seconds*hps.sr)//top_prior.raw_to_tokens)*top_prior.raw_to_tokens
x = load_prompts(audio_files, duration, hps)
zs = top_prior.encode(x, start_level=0, end_level=len(priors), bs_chunks=x.shape[0])
zs = sample_partial_window(zs, labels_1[2], labels_2[2], sampling_kwargs, 2, top_prior, tokens_to_sample, hps)
x = vqvae.decode(zs[2:], start_level=2).cpu().numpy()
# then comment out the zs= that comes next...

Sampling 3803 tokens for [0,3803]. Conditioning on 2411 tokens
380300.0%-ish, level 2
Primed sampling 3 samples with temp=0.98, top_k=0, top_p=0.0
151/151 [00:25<00:00,  5.85it/s]
1392/1392 [02:42<00:00,  8.59it/s]


In [ ]:
# non-primed 
zs=[t.zeros(hps.n_samples,0,dtype=t.long, device='cuda') for _ in range(3)]
zs=sample_partial_window(zs, labels_1[2], labels_2[2], sampling_kwargs, 2, top_prior, tokens_to_sample, hps)
x = vqvae.decode(zs[2:], start_level=2).cpu().numpy()

Listen to your generated samples, and then pick a favorite. If you don't like any, go back and rerun the cell above. 

** NOTE this is at the noisy top level, upsample fully (in the next section) to hear the final audio version

In [11]:
if not os.path.exists(hps.name):
  os.makedirs(hps.name)

for i in range(hps.n_samples):
  librosa.output.write_wav(f'{hps.name}noisy_top_level_generation_{i}.wav', x[i], sr=44100)



In [12]:
Audio(f'{hps.name}noisy_top_level_generation_0.wav')

In [13]:
Audio(f'{hps.name}noisy_top_level_generation_1.wav')

In [14]:
Audio(f'{hps.name}noisy_top_level_generation_2.wav')

If you don't like any of the options, return a few cells back to "Sample a few options..." and rerun from there.

## Choose your favorite sample and request longer generation

---

(Repeat from here)


In [16]:
ctr=0

** EITHER PROCEED **

In [101]:
my_choice = 2

ctr += 1
zs[2]=zs[2][my_choice].repeat(hps.n_samples,1)
t.save(zs, f'{hps.name}zs-checkpoint-{ctr}.t')

print(f'counter is at {ctr}')

counter is at 5


** OR GO BACK **

In [121]:
# checkpoint 1 is good
# checkpoint 3 is also good
num = 3
ctr = num
zs=t.load(f'{hps.name}zs-checkpoint-{num}.t') 

In [114]:
print(ctr)

3


Choose the length of the continuation.  The 1B model can generate up to 17 second samples and the 5B up to 23 seconds, but you'll want to pick a shorter continuation length so that it will be able to look back at what you've generated already.  Here we've chosen 4 seconds.

In [108]:
continue_generation_in_seconds=4
tokens_to_sample = seconds_to_tokens(continue_generation_in_seconds, hps.sr, top_prior, chunk_size)

The next step asks the top prior to generate more of the sample. It'll take up to a few minutes, depending on the sample length you request.

In [ ]:
zs = sample_partial_window(zs, labels_1[2], labels_2[2], sampling_kwargs, 2, top_prior, tokens_to_sample, hps)
x = vqvae.decode(zs[2:], start_level=2).cpu().numpy()

Sampling 7979 tokens for [0,7979]. Conditioning on 6587 tokens
797900.0%-ish, level 2
Primed sampling 3 samples with temp=0.98, top_k=0, top_p=0.0
391/412 [01:16<00:04,  4.20it/s]

Now listen to the longer versions of the sample you selected, and again choose a favorite sample.  If you don't like any, return back to the cell where you can load the checkpoint, and continue again from there.

When the samples start getting long, you might not always want to listen from the start, so change the playback start time later on if you like.

In [20]:
playback_start_time_in_seconds = 0

In [ ]:
for i in range(hps.n_samples):
  librosa.output.write_wav(f'{hps.name}top_level_continuation_{i}.wav', x[i][playback_start_time_in_seconds*44100:], sr=44100)

In [ ]:
Audio(f'{hps.name}top_level_continuation_0.wav')

In [ ]:
Audio(f'{hps.name}top_level_continuation_1.wav')

In [ ]:
Audio(f'{hps.name}top_level_continuation_2.wav')

To make a longer song, return back to "Choose your favorite sample" and loop through that again

# Upsample Co-Composition to Higher Audio Quality

Choose your favorite sample from your latest group of generations.  (If you haven't already gone through the Co-Composition block, make sure to do that first so you have a generation to upsample).

In [ ]:
choice = 2
select_best_sample = False  # Set false if you want to upsample all your samples 
                           # upsampling sometimes yields subtly different results on multiple runs,
                           # so this way you can choose your favorite upsampling

In [ ]:
if select_best_sample:
  zs[2]=zs[2][choice].repeat(zs[2].shape[0],1)

t.save(zs, f'{hps.name}zs-top-level-final.t')

Note: If you are using a CoLab hosted runtime on the free tier, you may want to download this zs-top-level-final.t file, and then restart an instance and load it in the next cell.  The free tier will last a maximum of 12 hours, and the upsampling stage can take many hours, depending on how long a sample you have generated.

In [ ]:
if False:
  zs = t.load(f'{hps.name}zs-top-level-final.t')

assert zs[2].shape[1]>=2048, f'Please first generate at least 2048 tokens at the top level, currently you have {zs[2].shape[1]}'
hps.sample_length = zs[2].shape[1]*top_prior.raw_to_tokens

In [ ]:
# Set this False if you are on a local machine that has enough memory (this allows you to do the
# lyrics alignment visualization). For a hosted runtime, we'll need to go ahead and delete the top_prior
# if you are using the 5b_lyrics model.
if True:
  del top_prior
  empty_cache()
  top_prior=None

upsamplers = [make_prior(setup_hparams(prior, dict()), vqvae, 'cpu') for prior in priors[:-1]]

In [ ]:
sampling_kwargs = [dict(temp=0.99, fp16=True, max_batch_size=16, chunk_size=32),
                   dict(temp=0.99, fp16=True, max_batch_size=16, chunk_size=32),
                   None]

# if type(labels_1[2])==dict:
labels_1 = [prior.labeller.get_batch_labels(metas_1, 'cuda') for prior in upsamplers] + [labels_1[2]]
labels_2 = [prior.labeller.get_batch_labels(metas_2, 'cuda') for prior in upsamplers] + [labels_2[2]] 

This next step upsamples 2 levels.  The level_1 samples will be available after around one hour (depending on the length of your sample) and are saved under {hps.name}/level_0/item_0.wav, while the fully upsampled level_0 will likely take 4-12 hours. You can access the wav files down below, or using the "Files" panel at the left of this CoLab.

(Please note, if you are using this CoLab on Google's free tier, you may want to download intermediate steps as the connection will last for a maximum 12 hours.)

In [ ]:
zs = upsample(zs, labels_1, labels_2, sampling_kwargs, [*upsamplers, top_prior], hps)

In [ ]:
Audio(f'{hps.name}level_0/item_0.wav')